
# BDTT Task 2: Recommender System

## Introduction

In this task,  I will train a collaborative filtering recommender system using a dataset from Steam, an online videogame distribution service. The dataset contains details of which games members have purchased and how long they played their purchased games, in hours. I will use the play duration data to train an Alternating Least Squares (ALS) model to generate recommendations. I will evaluate the performance of the model using the Root Mean Square Error (RMSE) metric and improve the model using a grid search to tune the hyperparameters. 

## Data Import and Preprocessing

I imported the dataset from a csv file into a dataframe. There were 200,000 rows in the dataframe and no null values. There were 707 duplicate rows, all of which concerned the purchase data, not the play duration data. I added a column to my dataframe containing unique integer IDs for the videogames. This is because the ALS model requires integer inputs and the videogame names provided are strings, not integers. I then split the dataframe into two: one for purchase data and one for play duration data.

In [0]:
# check csv file successfully uploaded into DBFS
dbutils.fs.ls("/FileStore/tables/steam_200k.csv")

[FileInfo(path='dbfs:/FileStore/tables/steam_200k.csv', name='steam_200k.csv', size=8059447, modificationTime=1743156953000)]

In [0]:
# inspect structure of csv file
for line in dbutils.fs.head("/FileStore/tables/steam_200k.csv").splitlines():
    print(line.find(","))
    print(line)

[Truncated to first 65536 bytes]
9
151603712,The Elder Scrolls V Skyrim,purchase,1
9
151603712,The Elder Scrolls V Skyrim,play,273
9
151603712,Fallout 4,purchase,1
9
151603712,Fallout 4,play,87
9
151603712,Spore,purchase,1
9
151603712,Spore,play,14.9
9
151603712,Fallout New Vegas,purchase,1
9
151603712,Fallout New Vegas,play,12.1
9
151603712,Left 4 Dead 2,purchase,1
9
151603712,Left 4 Dead 2,play,8.9
9
151603712,HuniePop,purchase,1
9
151603712,HuniePop,play,8.5
9
151603712,Path of Exile,purchase,1
9
151603712,Path of Exile,play,8.1
9
151603712,Poly Bridge,purchase,1
9
151603712,Poly Bridge,play,7.5
9
151603712,Left 4 Dead,purchase,1
9
151603712,Left 4 Dead,play,3.3
9
151603712,Team Fortress 2,purchase,1
9
151603712,Team Fortress 2,play,2.8
9
151603712,Tomb Raider,purchase,1
9
151603712,Tomb Raider,play,2.5
9
151603712,The Banner Saga,purchase,1
9
151603712,The Banner Saga,play,2
9
151603712,Dead Island Epidemic,purchase,1
9
151603712,Dead Island Epidemic,play,1.4
9
151603712,BioShock I

In [0]:
# create dataframe from csv file. Include quote='"' to ensure game names with commas in them are not split across multiple columns 

df = spark.read.csv("/FileStore/tables/steam_200k.csv", header=False, inferSchema=True, quote='"').toDF("memberID", "game", "purchplay", "hours")
steamDF = df
steamDF.show(10, truncate = False)

+---------+--------------------------+---------+-----+
|memberID |game                      |purchplay|hours|
+---------+--------------------------+---------+-----+
|151603712|The Elder Scrolls V Skyrim|purchase |1.0  |
|151603712|The Elder Scrolls V Skyrim|play     |273.0|
|151603712|Fallout 4                 |purchase |1.0  |
|151603712|Fallout 4                 |play     |87.0 |
|151603712|Spore                     |purchase |1.0  |
|151603712|Spore                     |play     |14.9 |
|151603712|Fallout New Vegas         |purchase |1.0  |
|151603712|Fallout New Vegas         |play     |12.1 |
|151603712|Left 4 Dead 2             |purchase |1.0  |
|151603712|Left 4 Dead 2             |play     |8.9  |
+---------+--------------------------+---------+-----+
only showing top 10 rows



In [0]:
steamDF.count()

200000

From the code above, I can see there are 200,000 rows in my dataframe (steamDF). Next I will check for null values. 

In [0]:
# Checking how many null values in each column

from pyspark.sql.functions import col, sum
steamDF.select([sum(col(c).isNull().cast("int")).alias(c) for c in steamDF.columns]).show()

+--------+----+---------+-----+
|memberID|game|purchplay|hours|
+--------+----+---------+-----+
|       0|   0|        0|    0|
+--------+----+---------+-----+



There are no null values in any of my columns. Next I will check for duplicate rows

In [0]:
# Checking for duplicate rows

import pyspark.sql.functions as F

# group the DataFrame by all columns, count the number of occurrences, and filter where the count is greater than 1
duplicates = steamDF.groupBy(steamDF.columns)\
    .count()\
    .where(F.col('count') > 1)

# count number of rows that have been duplicated 
duplicates.count()

707

The code above tells me there are 707 duplicate rows. I will inspect these more closely 

In [0]:
duplicates.show()

+---------+--------------------+---------+-----+-----+
| memberID|                game|purchplay|hours|count|
+---------+--------------------+---------+-----+-----+
|  9823354|Sid Meier's Civil...| purchase|  1.0|    2|
|  2259650|Sid Meier's Civil...| purchase|  1.0|    2|
| 56038151|Grand Theft Auto ...| purchase|  1.0|    2|
|142001340|Grand Theft Auto ...| purchase|  1.0|    2|
|152959594|Grand Theft Auto III| purchase|  1.0|    2|
| 50769696|Grand Theft Auto ...| purchase|  1.0|    2|
| 11813637|Sid Meier's Civil...| purchase|  1.0|    2|
| 65398650|Sid Meier's Civil...| purchase|  1.0|    2|
| 36502549|Sid Meier's Civil...| purchase|  1.0|    2|
| 80779496|Sid Meier's Civil...| purchase|  1.0|    2|
| 51557405|Grand Theft Auto ...| purchase|  1.0|    2|
|100351493|Sid Meier's Civil...| purchase|  1.0|    2|
|100351493|Sid Meier's Civil...| purchase|  1.0|    2|
|100351493|Sid Meier's Civil...| purchase|  1.0|    2|
|189858084|Grand Theft Auto ...| purchase|  1.0|    2|
| 69009454

From looking at 20 of the duplicate rows above, it would appear they are all of the 'purchase' type, not 'play' type. I will check this.

In [0]:
# check how many duplicates are of 'play' records rather than 'purchase' records 
play_duplicates = duplicates.where(duplicates.purchplay=='play')
play_duplicates.count()


0

The code above confirms there are no duplicate rows which contain 'play' in the 'purchplay' column. Since I will be using the 'play' rows to train my recommender system, I will ignore the duplicates in the 'purchase' rows for now. Next I will add a column containing an integer ID for each game (this will be necessary for training the recommender system, as the inputs need to be integers, not strings).

In [0]:
# generate a unique integer ID for each game (gameID) and add this into the dataframe (steamDF)

from pyspark.ml.feature import StringIndexer

indexer = StringIndexer(inputCol="game", outputCol="gameID")
steamDF_indexed = indexer.fit(steamDF).transform(steamDF)

steamDF_indexed.show(10, truncate = False)


🏃 View run monumental-hare-861 at: https://community.cloud.databricks.com/ml/experiments/2194890496938728/runs/77fbf61941974a9cbfd686b33aff0e50
🧪 View experiment at: https://community.cloud.databricks.com/ml/experiments/2194890496938728
+---------+--------------------------+---------+-----+------+
|memberID |game                      |purchplay|hours|gameID|
+---------+--------------------------+---------+-----+------+
|151603712|The Elder Scrolls V Skyrim|purchase |1.0  |8.0   |
|151603712|The Elder Scrolls V Skyrim|play     |273.0|8.0   |
|151603712|Fallout 4                 |purchase |1.0  |100.0 |
|151603712|Fallout 4                 |play     |87.0 |100.0 |
|151603712|Spore                     |purchase |1.0  |332.0 |
|151603712|Spore                     |play     |14.9 |332.0 |
|151603712|Fallout New Vegas         |purchase |1.0  |29.0  |
|151603712|Fallout New Vegas         |play     |12.1 |29.0  |
|151603712|Left 4 Dead 2             |purchase |1.0  |4.0   |
|151603712|Left 4 D

Next I will split my original dataframe steamDF into a 'purchase' dataframe and a 'play' dataframe.

In [0]:
# split dataframe into 2 dataframes: one for 'purchase' rows and one for 'play' rows 

# Import required modules 
from pyspark.sql import SparkSession 

# Create a SparkSession 
spark = SparkSession.builder.appName("Split DataFrame").getOrCreate() 

# Split the DataFrame into two 
purchase_df = steamDF_indexed.filter(steamDF_indexed['purchplay'] == 'purchase') 
play_df = steamDF_indexed.filter(steamDF_indexed['purchplay'] == 'play') 

# Print the new dataframes 
purchase_df.show(5, truncate=False) 
play_df.show(5, truncate=False)


+---------+--------------------------+---------+-----+------+
|memberID |game                      |purchplay|hours|gameID|
+---------+--------------------------+---------+-----+------+
|151603712|The Elder Scrolls V Skyrim|purchase |1.0  |8.0   |
|151603712|Fallout 4                 |purchase |1.0  |100.0 |
|151603712|Spore                     |purchase |1.0  |332.0 |
|151603712|Fallout New Vegas         |purchase |1.0  |29.0  |
|151603712|Left 4 Dead 2             |purchase |1.0  |4.0   |
+---------+--------------------------+---------+-----+------+
only showing top 5 rows

+---------+--------------------------+---------+-----+------+
|memberID |game                      |purchplay|hours|gameID|
+---------+--------------------------+---------+-----+------+
|151603712|The Elder Scrolls V Skyrim|play     |273.0|8.0   |
|151603712|Fallout 4                 |play     |87.0 |100.0 |
|151603712|Spore                     |play     |14.9 |332.0 |
|151603712|Fallout New Vegas         |play   

In [0]:
# check the number of rows in the two new dataframes equals number of rows in original dataframe

steamDF_rows = steamDF.count()
purchase_df_rows = purchase_df.count()
play_df_rows = play_df.count()

if purchase_df_rows + play_df_rows == steamDF_rows:
    print("it worked")
else: 
    print("it didn't work")

it worked


In [0]:
# check all 'hours' values in purchase_df are equal to 1 (to check that none of the 'play duration' rows were inaccurately labelled as 'purchase')

purchase_df.groupBy("hours").count().display()

hours count 1.0 129511

Next I drop the 'purchplay' column from both new dataframes and 'hours' column from purchase dataframe as they're no longer needed (and might slow down processing if kept in)

In [0]:
dropped_purchase_df = purchase_df.drop("purchplay").drop("hours")
dropped_play_df = play_df.drop("purchplay") 

dropped_purchase_df.show(5, truncate=False) 
dropped_play_df.show(5, truncate=False)

+---------+--------------------------+------+
|memberID |game                      |gameID|
+---------+--------------------------+------+
|151603712|The Elder Scrolls V Skyrim|8.0   |
|151603712|Fallout 4                 |100.0 |
|151603712|Spore                     |332.0 |
|151603712|Fallout New Vegas         |29.0  |
|151603712|Left 4 Dead 2             |4.0   |
+---------+--------------------------+------+
only showing top 5 rows

+---------+--------------------------+-----+------+
|memberID |game                      |hours|gameID|
+---------+--------------------------+-----+------+
|151603712|The Elder Scrolls V Skyrim|273.0|8.0   |
|151603712|Fallout 4                 |87.0 |100.0 |
|151603712|Spore                     |14.9 |332.0 |
|151603712|Fallout New Vegas         |12.1 |29.0  |
|151603712|Left 4 Dead 2             |8.9  |4.0   |
+---------+--------------------------+-----+------+
only showing top 5 rows



In [0]:
dropped_purchase_df.count()

129511

In [0]:

dropped_play_df.count()

70489

From the last 2 lines of code, I can see that there are fewer rows in the 'play' dataframe than the 'purchase' dataframe. This is as I'd expect, as not all games that are purchased will necessarily be played. However, every game that is played must first have been purchased (so the 'play' set is a subset of the 'purchase' set). Lastly, I will check if there are any rows in the 'play' dataframe that conatin 0 hours of play.

In [0]:
# Check if any rows in the play duration dataframe contain 0.0 hours of play 

zero_hours_count = dropped_play_df.filter(dropped_play_df.hours == 0.0).count()
print("Number of rows with 0.0 hours:", zero_hours_count)

Number of rows with 0.0 hours: 0


## Exploratory Data Analysis (EDA)

In this EDA section, I explored the ranges and trends of my dataset. For example, I investigated which members purchased the most games, which games were most and least purchased, and which members and games had the longest and shortest play durations. Range in play duration will be particularly relevant for informing how I train my recommender system since ALS models are most accurate when their numerical inputs are evenly distributed. If the play duration is highly skewed, then the long play duration values could disproportionately influence the model, leading it to overemphasize heavy players and therefore making less accurate predictions and recommendations. 

### EDA of purchase data

In [0]:
# which members purchased the most games

member_purchase_df = dropped_purchase_df.groupBy("memberID").count().sort("count", ascending=False)

display(member_purchase_df)


memberID count 62990992 1075 33865373 783 30246419 766 58345543 667 76892907 597 20772968 595 11403772 592 64787956 591 22301321 568 47457723 557 33013552 520 53875128 505 86469479 480 49893565 477 11373749 458 24721232 456 138941587 448 36546868 430 59825286 428 122026623 419 36557643 416 24469287 415 154230723 413 48798067 399 116876958 396 975449 378 58905429 374 36404933 366 86912006 348 21061921 340 65398650 335 38049880 326 8585433 316 69954842 314 17530772 307 14465359 305 51557405 303 81943620 301 44472980 295 12610800 292 31669242 289 11149819 287 40212239 281 26762388 281 9128105 276 298950 259 10599862 257 87694960 255 88579585 254 87734805 251 86055705 250 50818751 246 16645459 244 69009454 243 92914917 238 46028967 237 55426012 235 55906572 232 10253354 232 33651880 228 70408902 228 148362155 227 47384202 226 78309377 225 107452765 221 154230933 221 61676491 218 155919035 216 77214425 215 11794760 209 2259650 203 49462664 202 78341587 197 11978743 196 30440303 196 60859695 195 49228258 193 71510748 192 9823354 190 73835640 189 24632218 188 180901075 187 13565651 186 27279261 185 135400225 185 22371742 180 116564064 180 44314169 178 56038151 177 30425578 177 99077905 177 59662830 177 53091150 175 37422528 174 155673786 173 43684632 172 43913966 172 101690993 172 57603447 170 134322141 170 159800136 170 118541865 169 11161178 169 77980915 169 83770731 169 51822361 168 99264709 167 43360645 165 187463594 165 45617627 164 43955374 163 88035166 162 67579257 162 166863117 161 72842694 159 34177747 159 13190476 159 81439192 159 55367062 158 42657809 158 60611062 158 39622853 157 34919318 157 77194239 157 60608576 157 157636450 157 35701646 154 28472068 154 64973908 152 1936551 152 118852041 152 47384303 152 92593907 151 62878249 150 124725852 150 81160212 150 105503045 150 17995238 149 561758 148 53898495 145 71527252 145 17567828 144 16084897 144 48028873 143 58931437 143 39037163 142 65754991 142 80128229 140 33282871 139 90272527 139 59925638 138 71777065 137 102825821 136 32126281 136 117531196 135 48984158 133 81170946 133 65958466 132 156565178 132 54310644 132 111754806 131 132300630 131 26729643 130 46637811 130 143877335 130 73726855 130 113752996 129 88525821 129 80779496 129 83849502 129 38317154 129 82263745 129 197904909 127 65117175 127 44545959 127 189734107 126 48525807 126 86041729 125 216088282 124 33622085 124 54637394 124 14126086 124 80189887 123 129117376 123 6717871 122 172518437 122 112626210 122 127628725 121 53097340 121 84455820 120 66650717 119 16154372 119 152959594 118 124059151 118 2753525 118 10450544 118 7907686 118 204795948 117 93275329 117 248444377 117 115632831 117 34901647 117 114727578 116 42061089 115 243664576 114 81585721 114 76451157 114 80494893 113 124437057 112 42005897 112 127272741 111 219466905 110 136135322 110 27403206 110 101878879 110 168163793 110 19696244 110 246439849 109 31187179 109 30912860 109 91690667 108 144071257 108 63441290 108 166669789 108 176771895 107 210905793 107 57770056 107 11731710 105 14544587 105 66255019 105 127335438 105 86481908 105 60296891 104 92393218 104 94936385 104 12144171 104 126191291 104 61632730 103 82352462 103 73564778 103 162288536 102 131348564 102 72978546 102 150033540 102 51085779 101 49050405 101 63157803 101 41559627 101 11940338 100 39361297 100 96588736 99 57103808 99 105877396 99 19085114 99 3449240 98 156675178 98 25096601 98 65145468 98 82287546 98 198735293 98 147602462 97 127072755 97 67729331 97 193156880 96 8259307 96 75155353 96 79073449 96 32467994 95 54826284 95 100311267 95 67694595 95 119619506 95 30061970 95 193103684 95 15196746 94 130312302 94 14962163 94 189858084 93 55975168 93 29239329 93 61506388 93 132748085 93 62705916 92 171067153 92 30519870 92 100894366 92 96400571 91 42771635 91 82046939 91 218317467 91 115996656 91 101695880 91 50744279 90 87341384 90 182399789 89 33706322 89 94269421 89 61189155 89 103371488 88 85366890 88 26465134 88 92612763 88 29753085 88 105384518 87 101596530 87 44866715 8

Databricks visualization. Run in Databricks to view.

In [0]:
# check highest 3 and lowest 3 values for games purchased by members. 
member_purchase_df.show(3)

member_purchase_df.tail(3)

+--------+-----+
|memberID|count|
+--------+-----+
|62990992| 1075|
|33865373|  783|
|30246419|  766|
+--------+-----+
only showing top 3 rows



[Row(memberID=251093449, count=1),
 Row(memberID=24817862, count=1),
 Row(memberID=127724511, count=1)]

From the histogram above, I can see there is quite a wide range in the nubmer of games purchased by each member. From the table, I can see the highest number of games purchased by an individual member is 1,075, followed by 783 and 766. The 3 lowest puchases were all 1 game per member. To note: I haven't eliminated duplicate rows from this dataframe, so some of these rows will include the same customer buying the same game more than once.

In [0]:
# check which games are most and least purchased 

game_purchase_df = dropped_purchase_df.groupBy("game").count().sort("count", ascending=False).limit(10)

display(game_purchase_df)

game count Dota 2 4841 Team Fortress 2 2323 Unturned 1563 Counter-Strike Global Offensive 1412 Half-Life 2 Lost Coast 981 Counter-Strike Source 978 Left 4 Dead 2 951 Counter-Strike 856 Warframe 847 Half-Life 2 Deathmatch 823

Databricks visualization. Run in Databricks to view.

In [0]:
# check 3 most purchased games and 3 least purchased games  
game_purchase_df.show(3)

game_purchase_df.tail(3)

+---------------+-----+
|           game|count|
+---------------+-----+
|         Dota 2| 4841|
|Team Fortress 2| 2323|
|       Unturned| 1563|
+---------------+-----+
only showing top 3 rows



[Row(game='Counter-Strike', count=856),
 Row(game='Warframe', count=847),
 Row(game='Half-Life 2 Deathmatch', count=823)]

From the bar chart above, we can see the most purchased game (Dota 2) has a far higher number of purchases (4,841) than the next 9 most-purchased games.  To note: I haven't eliminated duplicate rows, so some of these rows will include the same customer buying a game more than once 

### EDA of play data

In [0]:
# Check which members and games have the longest play times

dropped_play_df.orderBy("hours", ascending=False).display()

memberID game hours gameID 73017395 Sid Meier's Civilization V 11754.0 11.0 100630947 Dota 2 10442.0 0.0 153382649 Team Fortress 2 9640.0 1.0 130882834 Dota 2 7765.0 0.0 52567955 Dota 2 6964.0 0.0 121199670 Dota 2 6753.0 0.0 86256882 Dota 2 6015.0 0.0 70487610 Sid Meier's Civilization V 6013.0 11.0 101414179 Dota 2 5982.0 0.0 12660489 Dota 2 5970.0 0.0 95758079 Dota 2 5866.0 0.0 93950791 Sid Meier's Civilization V 5720.0 11.0 67694595 Dota 2 5608.0 0.0 106099216 Sid Meier's Civilization V 5483.0 11.0 117106617 Dota 2 5229.0 0.0 98308239 Dota 2 5142.0 0.0 128065805 Sid Meier's Civilization V 5002.0 11.0 20207081 Dota 2 4845.0 0.0 167194020 FINAL FANTASY XIV A Realm Reborn 4835.0 805.0 32749624 Counter-Strike 4814.0 6.0 102376253 Dota 2 4785.0 0.0 145606876 Football Manager 2014 4775.0 262.0 63615483 APB Reloaded 4749.0 78.0 120725727 Dota 2 4694.0 0.0 49312497 Counter-Strike Source 4676.0 5.0 22283916 Counter-Strike 4664.0 6.0 135879753 Counter-Strike Global Offensive 4659.0 2.0 125912054 Dota 2 4617.0 0.0 164643993 Dota 2 4462.0 0.0 57905818 Counter-Strike Source 4405.0 5.0 50811344 Dota 2 4335.0 0.0 133719158 Dota 2 4320.0 0.0 155182551 Dota 2 4228.0 0.0 121900241 Counter-Strike 4217.0 6.0 126388107 Dota 2 4122.0 0.0 137222368 Dota 2 4074.0 0.0 141706846 Dota 2 4067.0 0.0 125017535 Counter-Strike Global Offensive 4021.0 2.0 88290913 Dota 2 3940.0 0.0 52731290 Baldur's Gate II Enhanced Edition 3898.0 1243.0 41719717 Counter-Strike 3840.0 6.0 108315158 Dota 2 3790.0 0.0 113444723 Dota 2 3744.0 0.0 92914917 Dota 2 3738.0 0.0 58481977 Dota 2 3735.0 0.0 103804924 Dota 2 3704.0 0.0 105586920 Dota 2 3695.0 0.0 133024750 Dota 2 3692.0 0.0 98839983 Dota 2 3672.0 0.0 119937035 Garry's Mod 3667.0 7.0 43684632 Counter-Strike Global Offensive 3626.0 2.0 120852852 Dota 2 3590.0 0.0 64060101 Dota 2 3539.0 0.0 17017968 Team Fortress 2 3503.0 1.0 127461395 Dota 2 3481.0 0.0 156946266 Dota 2 3458.0 0.0 37422528 Counter-Strike Global Offensive 3416.0 2.0 139673932 Football Manager 2013 3374.0 189.0 66403743 Counter-Strike 3368.0 6.0 87740709 Dota 2 3356.0 0.0 103563010 Dota 2 3353.0 0.0 99077905 Dota 2 3309.0 0.0 92593907 Dota 2 3289.0 0.0 53244117 Counter-Strike 3283.0 6.0 111362598 Dota 2 3252.0 0.0 48798067 Mount & Blade Warband 3178.0 153.0 71871620 Counter-Strike 3169.0 6.0 172105480 Dota 2 3116.0 0.0 111551727 Dota 2 3085.0 0.0 114112364 Dota 2 3047.0 0.0 23492094 Dota 2 3038.0 0.0 57433226 Counter-Strike Source 3013.0 5.0 155069128 Dota 2 3010.0 0.0 117488479 Dota 2 2989.0 0.0 113423671 Dota 2 2979.0 0.0 49380630 Counter-Strike Source 2965.0 5.0 125141344 Team Fortress 2 2956.0 1.0 53964834 Counter-Strike 2903.0 6.0 190754099 Dota 2 2891.0 0.0 47291376 Counter-Strike 2889.0 6.0 161444156 Dota 2 2865.0 0.0 58223726 Counter-Strike 2857.0 6.0 109393227 Dota 2 2857.0 0.0 59662830 Dota 2 2852.0 0.0 142489812 Europa Universalis IV 2836.0 401.0 144532046 Dota 2 2758.0 0.0 86912006 Dota 2 2755.0 0.0 158693714 Dota 2 2741.0 0.0 38317154 Dota 2 2730.0 0.0 12195913 Left 4 Dead 2 2710.0 4.0 169560266 Dota 2 2700.0 0.0 157314597 Dota 2 2691.0 0.0 136783755 Dota 2 2682.0 0.0 173846745 Dota 2 2672.0 0.0 125324040 Dota 2 2666.0 0.0 155673786 Dota 2 2653.0 0.0 30036927 Team Fortress 2 2653.0 1.0 82263745 Dota 2 2634.0 0.0 47887890 Counter-Strike Source 2633.0 5.0 52731290 Baldur's Gate Enhanced Edition 2630.0 744.0 61189155 Dota 2 2623.0 0.0 112647787 Dota 2 2609.0 0.0 41606445 Counter-Strike 2605.0 6.0 54916182 Football Manager 2010 2603.0 555.0 148928721 Dota 2 2594.0 0.0 72329360 Sid Meier's Civilization V 2589.0 11.0 101487265 Dota 2 2582.0 0.0 16080105 Counter-Strike 2571.0 6.0 143137329 Dota 2 2566.0 0.0 46637811 Dota 2 2563.0 0.0 127074858 Dota 2 2531.0 0.0 78799565 Counter-Strike 2526.0 6.0 122679931 Team Fortress 2 2522.0 1.0 57433226 Counter-Strike Global Offensive 2508.0 2.0 10302000 Football Manager 2015 2503.0 265.0 153156310 Dota 2 2496.0 0.0 100519466 Arma 3 2484.0 110.0 48984158 Dota 2 2458.0 0.0 11403772 Dota 2 2443.0 0.0 121352371 Dota 

In [0]:
# HOW TO VISUALISE ABOVE? 

In [0]:
# see which member played the most hours across all games
member_play_df = dropped_play_df.drop("game").drop("gameID")

from pyspark.sql import functions as F

# Group by 'memberID', sum the 'hours', and sort in descending order
aggregated_df = member_play_df.groupBy("memberID") \
                  .agg(F.round(F.sum("hours"),3).alias("total_hours")) \
                  .orderBy(F.desc("total_hours"))

# Show the result
display(aggregated_df)


memberID total_hours 73017395 11754.0 10599862 11651.7 100630947 10853.2 26762388 10470.1 153382649 9640.0 43684632 9546.3 48798067 9427.2 52731290 9417.6 42935819 8172.9 14544587 8137.1 52567955 7836.7 130882834 7801.9 57433226 7741.5 63615483 7190.4 47063596 7161.0 67694595 7152.1 17017968 7108.5 50818751 6929.9 49893565 6891.9 24721232 6887.0 99077905 6838.4 121199670 6827.2 42849279 6766.2 81054122 6470.0 32126281 6362.6 49312497 6356.0 70487610 6325.5 86256882 6312.7 50811344 6171.3 43955374 6094.3 42657809 6093.4 12660489 6074.1 11403772 6009.9 101414179 5982.0 167194020 5930.0 95758079 5866.0 8585433 5856.6 17995238 5808.8 87201181 5792.4 34177747 5776.3 106099216 5739.8 62990992 5724.8 93950791 5720.0 57905818 5534.8 49380630 5525.9 32467994 5459.2 103260848 5419.3 42363887 5384.3 128065805 5366.0 23492094 5346.8 15415372 5331.7 20207081 5316.4 64392327 5301.0 120725727 5297.8 48525807 5260.0 112845094 5240.8 101596530 5232.8 117106617 5229.0 111362598 5205.3 131610144 5191.6 78799565 5186.9 98308239 5144.1 41719717 5128.6 59925638 5052.9 121900241 5038.8 43360645 5030.4 46637811 4958.6 32749624 4937.3 125912054 4923.6 145606876 4916.2 61189155 4894.7 113752996 4876.7 92593907 4855.2 10302000 4849.5 47457723 4844.3 135879753 4810.0 63157803 4801.2 102376253 4785.0 133024750 4771.6 66650717 4764.1 175001491 4729.6 82263745 4686.8 22283916 4681.7 26729643 4672.8 125017535 4635.3 37422528 4583.3 59662830 4563.7 101339059 4496.4 74347105 4496.3 92914917 4483.9 133719158 4474.7 164643993 4468.9 14465359 4405.5 24919113 4375.8 37723786 4370.2 117488479 4360.7 126388107 4340.0 137222368 4246.8 155182551 4228.0 44472980 4221.9 33651880 4219.5 47291376 4175.7 52321307 4118.5 62705916 4082.3 38049880 4076.5 38317154 4068.3 141706846 4067.0 40080833 4057.9 119937035 4053.6 88290913 4043.4 75368808 4019.1 127272741 4013.1 17649444 4001.9 11731710 3980.0 55906572 3960.6 86912006 3960.1 11373749 3943.2 7955670 3927.9 58481977 3923.6 105586920 3909.8 46951849 3882.0 111551727 3843.1 39037163 3826.6 65152385 3826.2 46030552 3819.6 30913209 3812.1 127461395 3795.0 108315158 3790.0 77214425 3785.8 103804924 3772.5 27279261 3762.2 113444723 3749.3 298950 3745.4 35701646 3699.3 87740709 3680.4 98839983 3672.0 252044076 3636.8 64060101 3625.9 33622085 3610.0 44545959 3602.6 120852852 3594.3 100519466 3584.3 87040683 3570.6 148362155 3568.8 60611062 3557.8 62078957 3520.5 79411077 3520.2 8776918 3508.8 56436338 3506.0 58761868 3499.7 103563010 3491.4 153156310 3490.3 139673932 3487.6 156946266 3485.4 103445207 3460.7 76032287 3453.5 94936385 3443.9 55975168 3382.2 66403743 3369.5 48984158 3346.3 86732465 3345.9 62878249 3291.7 53244117 3284.1 49767455 3271.9 71871620 3259.9 69856757 3232.9 59536273 3227.6 53898495 3227.3 36546868 3222.6 80511960 3214.9 173940259 3214.0 172105480 3212.4 14126086 3202.7 17567828 3200.9 23154676 3189.7 87071236 3180.6 113423671 3177.3 60608576 3175.2 66596291 3165.4 54826284 3161.2 96400571 3149.9 122679931 3134.1 43913966 3118.0 30519870 3101.3 144455775 3065.4 53711793 3062.8 121497634 3062.6 155673786 3061.7 122026623 3056.3 71510748 3049.9 13190476 3049.8 114112364 3047.0 99255590 3043.4 51822361 3035.2 121360145 3020.1 42005897 3013.4 138941587 3011.2 155069128 3010.0 47887890 3008.3 125141344 3008.2 92393218 2986.6 31669242 2976.5 58223726 2974.0 162288536 2973.1 137158399 2971.5 50797633 2948.7 190754099 2919.0 53964834 2903.0 11161178 2898.4 131940023 2895.2 161444156 2891.9 109393227 2889.0 151600301 2885.2 19696244 2883.1 118852041 2877.1 70778973 2859.3 124810250 2855.3 17530772 2845.6 165779930 2837.0 142489812 2836.0 12195913 2834.2 160427210 2826.2 124443679 2824.9 116876958 2824.3 11149819 2816.7 78309377 2815.8 80189887 2814.1 51085779 2807.5 80128229 2803.7 187463594 2800.1 36502549 2799.9 11813637 2799.1 80384872 2798.7 75598925 2796.6 104721942 2793.0 190191843 2773.7 126340495 2770.9 144532046 2766.2 63702300 2758.9 67713900 2748.6 72717958 2746.5 194970068 2744.5 158693714 2741.0 9823354 2

Databricks visualization. Run in Databricks to view.

In [0]:
# Check memberIDs with 3 highest and 3 lowest play durations (across all games)

aggregated_df.show(3)
aggregated_df.tail(3)

+---------+-----------+
| memberID|total_hours|
+---------+-----------+
| 73017395|    11754.0|
| 10599862|    11651.7|
|100630947|    10853.2|
+---------+-----------+
only showing top 3 rows



[Row(memberID=85395339, total_hours=0.1),
 Row(memberID=289193172, total_hours=0.1),
 Row(memberID=74859759, total_hours=0.1)]

The code above shows there is very high variance in the hours column (0.1 hours to 11,754 hours). This might cause problems for the recommender system I will build, since ALS models work best when numerical values are more evenly distributed and not so highly skewed. The ALS might overfit to users who have extremely high play durations, which will mean the predictions are not generalisable across users with lower play durations. 

In [0]:
# see which game was played the most hours across all members 

game_play_df = dropped_play_df.drop("memberID").drop("gameID")

# Group by 'game', sum the 'hours', and sort in descending order
aggregated_df2 = game_play_df.groupBy("game") \
                  .agg(F.round(F.sum("hours"),3).alias("total_hours")) \
                  .orderBy(F.desc("total_hours"))

# Show the result
aggregated_df2.display()

game total_hours Dota 2 981684.6 Counter-Strike Global Offensive 322771.6 Team Fortress 2 173673.3 Counter-Strike 134261.1 Sid Meier's Civilization V 99821.3 Counter-Strike Source 96075.5 The Elder Scrolls V Skyrim 70889.3 Garry's Mod 49725.3 Call of Duty Modern Warfare 2 - Multiplayer 42009.9 Left 4 Dead 2 33596.7 Football Manager 2013 32308.6 Football Manager 2012 30845.8 Football Manager 2014 30574.8 Terraria 29951.8 Warframe 27074.6 Football Manager 2015 24283.1 Arma 3 24055.7 Grand Theft Auto V 22956.7 Borderlands 2 22667.9 Empire Total War 21030.3 Total War ROME II - Emperor Edition 20892.5 Mount & Blade Warband 20636.8 Call of Duty Modern Warfare 3 - Multiplayer 20603.0 DayZ 20315.4 PAYDAY 2 19613.8 Call of Duty Black Ops - Multiplayer 17144.5 Unturned 16096.4 Total War SHOGUN 2 15761.5 Rust 15275.3 Fallout New Vegas 14832.9 War Thunder 14381.6 Call of Duty Black Ops II - Multiplayer 13816.3 ARK Survival Evolved 13593.1 Football Manager 2010 13126.7 Clicker Heroes 12937.4 Football Manager 2011 11336.8 Fallout 4 10762.8 Path of Exile 10185.6 Napoleon Total War 9966.0 Europa Universalis IV 9759.0 Arma 2 Operation Arrowhead 9429.7 APB Reloaded 9237.2 Portal 2 9117.1 Robocraft 9096.6 Crusader Kings II 9020.7 Left 4 Dead 8659.9 Call of Duty Modern Warfare 2 8635.4 Killing Floor 8171.1 Counter-Strike Condition Zero 7950.0 Rocket League 7827.2 XCOM Enemy Unknown 7696.1 Football Manager 2009 7434.4 H1Z1 7364.2 Euro Truck Simulator 2 7226.9 Torchlight II 6891.9 Age of Empires II HD Edition 6858.5 The Binding of Isaac Rebirth 6735.5 Battlefield Bad Company 2 6678.6 FINAL FANTASY XIV A Realm Reborn 6618.5 PlanetSide 2 6239.7 DARK SOULS II 6193.8 AdVenture Capitalist 6067.7 The Binding of Isaac 5458.1 Call of Duty Modern Warfare 3 5443.6 Rising Storm/Red Orchestra 2 Multiplayer 5412.5 Kerbal Space Program 5334.5 Starbound 5189.8 Far Cry 3 5076.0 Warhammer 40,000 Dawn of War II Retribution 4983.7 Saints Row The Third 4954.1 Tom Clancy's Ghost Recon Phantoms - NA 4910.8 The Witcher 3 Wild Hunt 4876.9 Day of Defeat Source 4840.3 Trove 4818.4 METAL GEAR SOLID V THE PHANTOM PAIN 4751.1 Borderlands 4742.8 Dark Souls Prepare to Die Edition 4738.5 Stronghold Kingdoms 4703.1 Grand Theft Auto IV 4686.3 DC Universe Online 4674.7 Space Engineers 4467.1 Baldur's Gate II Enhanced Edition 4277.3 Half-Life 2 4260.3 Sid Meier's Civilization IV Beyond the Sword 4201.4 Might & Magic Heroes VI 4139.5 7 Days to Die 4075.5 Chivalry Medieval Warfare 3964.4 Call of Duty Black Ops 3876.0 Dungeon Defenders 3816.2 Call of Duty Ghosts - Multiplayer 3804.6 Half-Life 2 Deathmatch 3712.9 BioShock Infinite 3689.1 Deus Ex Human Revolution 3587.4 Don't Starve 3581.9 Star Trek Online 3501.1 Just Cause 2 3457.5 Neverwinter 3451.5 Warhammer 40,000 Dawn of War II 3444.1 Heroes & Generals 3299.5 Medieval II Total War 3284.0 The Witcher Enhanced Edition 3257.5 The Witcher 2 Assassins of Kings Enhanced Edition 3254.3 Tom Clancy's Ghost Recon Phantoms - EU 3234.3 Assassin's Creed IV Black Flag 3230.3 Marvel Heroes 2015 3219.8 Cities Skylines 3201.2 Tomb Raider 3184.3 RIFT 3113.6 Call of Duty Advanced Warfare - Multiplayer 3096.4 Baldur's Gate Enhanced Edition 3094.9 Train Simulator 2975.5 Mafia II 2893.4 Borderlands The Pre-Sequel 2852.1 Dishonored 2842.2 Sid Meier's Civilization Beyond Earth 2826.6 NBA 2K15 2714.7 Total War ATTILA 2654.7 Banished 2631.0 Prison Architect 2626.5 Mass Effect 2609.8 Mortal Kombat X 2598.1 Call of Duty World at War 2583.5 Saints Row IV 2563.0 Dragon Age Origins - Ultimate Edition 2552.5 Assassin's Creed III 2545.4 Dead Island 2532.0 Pro Evolution Soccer 2015 2500.5 Natural Selection 2 2498.9 Mass Effect 2 2492.0 Elite Dangerous 2455.7 Zombie Panic Source 2440.7 Plants vs. Zombies Game of the Year 2427.6 Rome Total War 2396.6 TERA 2388.1 Divinity Original Sin 2380.1 Supreme Commander 2 2361.5 Spiral Knights 2360.7 Middle-earth Shadow of Mordor 2324.5 Insurgency 2317.1 FTL Faster Than Light 2315.8 Football Manager 2016 2296.6 Portal 2282.8 Trans

In [0]:
# HOW TO VISUALISE ABOVE? 

In [0]:
# Check games with 3 highest and 3 lowest play durations (across all members)

aggregated_df2.show(3)
aggregated_df2.tail(3)

+--------------------+-----------+
|                game|total_hours|
+--------------------+-----------+
|              Dota 2|   981684.6|
|Counter-Strike Gl...|   322771.6|
|     Team Fortress 2|   173673.3|
+--------------------+-----------+
only showing top 3 rows



[Row(game='D.U.S.T.', total_hours=0.1),
 Row(game='Habitat', total_hours=0.1),
 Row(game='Sandmason', total_hours=0.1)]

In [0]:
# calculate mean playing time 

from pyspark.sql import functions as F
dropped_play_df.agg(F.mean('hours')).collect()[0][0]

48.87806324391008

In [0]:
# HOW TO VISUALISE ABOVE? 

The mean duration of play is 48.88 hours. 

## Model Training

In this section, I split the play duration dataframe I created at the end of the 'data import and pre-processing' section above into training and test sets. I then train an Alternating Least Squares (ALS) algorithm on a training dataset using arbitrary hyperparameters. 

In [0]:
# import mlflow and autolog machine learning runs to track experiments 
import mlflow

mlflow.pyspark.ml.autolog()

In [0]:
# split data in dataframe contianing only play records (dropped_play_df) into training and test dataset 

(training, test) = dropped_play_df.randomSplit([0.8, 0.2], seed=100)

In [0]:
# Apply the Alternating Least Squares (ALS) algorithm. Instantiate an instance of the estimator and specify the columns in the dataframe which are the userCol, itemCol, and ratingCol. Set nonnegative to True to avoid predictions that are negative integers (can't have a negative number of playing hours)

from pyspark.ml.recommendation import ALS

als = ALS(maxIter=5, regParam=0.01, userCol="memberID", itemCol="gameID", ratingCol='hours', seed=100)

# Use the fit() method to train the model on the training dataset 
model = als.fit(training)

2025/04/06 09:05:45 INFO mlflow.utils.autologging_utils: Created MLflow autologging run with ID 'fe8bb598127d4753b2ecf52cc00c77ee', which will track hyperparameters, performance metrics, model artifacts, and lineage information for the current pyspark.ml workflow
2025/04/06 09:05:46 WARNING mlflow.utils.autologging_utils: MLflow autologging encountered a warning: "/databricks/python/lib/python3.11/site-packages/mlflow/types/utils.py:435: UserWarning: Hint: Inferred schema contains integer column(s). Integer columns in Python cannot represent missing values. If your input data contains missing values at inference time, it will be encoded as floats and will cause a schema enforcement error. The best way to avoid this problem is to infer the model schema based on a realistic data sample (training dataset) that includes missing values. Alternatively, you can declare integer columns as doubles (float64) whenever these columns may have missing values. See `Handling Integers With Missing Valu

🏃 View run whimsical-swan-552 at: https://community.cloud.databricks.com/ml/experiments/2194890496938728/runs/fe8bb598127d4753b2ecf52cc00c77ee
🧪 View experiment at: https://community.cloud.databricks.com/ml/experiments/2194890496938728


Running the code above led to the run being logged as an experiment in MLflow

## Model Evaluation

In this section, I evaluate the ALS model trained in the section above by using it to generate predictions on the test dataset. I then evaluate the accuracy of these predictions, as compared to the actual values in the test dataset, using the Root Mean Square Error (RMSE) metric. 

In [0]:
# Use trained model to make predictions on the test dataset. The model is unable to make predictions for members who did not have any reviews in the training dataset (the cold start problem). For these users the predictions will be NaN, so I use dropna() to remove these rows from the predictions DataFrame

predictions = model.transform(test).dropna()

predictions.show()

+--------+--------------------+-----+------+----------+
|memberID|                game|hours|gameID|prediction|
+--------+--------------------+-----+------+----------+
|    5250|              Dota 2|  0.2|     0|  266.0414|
|   76767|Call of Duty Blac...| 12.5|    57| 1414.4698|
|   76767|Call of Duty Mode...|  9.7|    62| 1958.2737|
|   76767|            Portal 2| 15.0|    15| 16.805851|
|   76767|    Worms Armageddon|  0.4|   634|10.4597645|
|  298950|ARK Survival Evolved| 41.0|   105| 452.80072|
|  298950|         Alien Swarm|  1.6|    32|  6.061899|
|  298950|      Alpha Protocol|  0.7|   816| 32.746536|
|  298950|Amnesia The Dark ...|  7.0|    97| 0.7135702|
|  298950|            Banished|  0.6|   214|-31.345238|
|  298950|Batman Arkham Ori...| 15.2|   146| 62.766155|
|  298950|     Castle Crashers|  2.9|   102| 5.6525035|
|  298950|Counter-Strike So...|  0.5|     5|  571.3417|
|  298950|   Crusader Kings II|  1.0|   215| 1393.0398|
|  298950|       Darksiders II| 22.0|   225|  65

In the 'predictions' column above, I can see negative integers, which doesn't make sense as it's not possible to have a negative play durnation. 

Next I will evaluate how accurate these predictions are. I will use Root Mean Square Error as the evaluation metric. This is a metric which is commonly used in regression and measures the average difference between the values predicted by a model and the actual values in the data.

In [0]:
# instantiate an evaluator which will use an evaluation metric (root mean square error) to  measure how effective the model is. 

from pyspark.ml.evaluation import RegressionEvaluator

evaluator = RegressionEvaluator(metricName="rmse", labelCol="hours", predictionCol="prediction")

rmse = evaluator.evaluate(predictions)

print("Root Mean Square Error is %g" %rmse)

Root Mean Square Error is 561.028


The code above gives an RMSE value of 561. This is the average difference between the values the model predicited for the number of hours played and the true values for these predictions. This difference is quite high. I will attempt to reduce it by improving the accuracy of my model.

## Hyperparameter Tuning and Other Accuracy Improvements 
In this section, I will make several adjustments to improve the accuracy of my ALS model. These inlcude: 

- only use data from players who played 4 or more games to train the model 
- eliminating negative predictions and recommendations from the model (since it's impossible to have a negative game playing duration)
- hyperparameter tuning using a grid search


In [0]:
# Count number of unique members in 'dropped_play_df' dataframe 
member_play_count = dropped_play_df.groupBy("memberID").count()
member_play_count.count()

11350

The code above shows there are 11,350 unique members in the 'dropped_play_df' dataframe (the one containing data on play duration, not purchases)

In [0]:
# From play duration dataset, filter out members who have played fewer than 5 games. If many members have played only a few games, ALS might struggle with recommendations.

filtered_df = dropped_play_df.groupBy("memberID").count().filter("count >= 5")
filtered_df.show()



+---------+-----+
| memberID|count|
+---------+-----+
| 16167221|   25|
|152861732|   12|
|208061820|    5|
|187877855|    6|
|119310413|   27|
|132418423|   10|
| 84471496|   17|
| 95059220|   10|
|100519466|   34|
| 78332414|   27|
| 57433226|   17|
|191747590|    6|
|272181160|    6|
| 55319994|    5|
| 65610147|   10|
|234024191|   13|
| 49724738|    5|
| 19616379|    5|
|170172944|   18|
|199628395|   20|
+---------+-----+
only showing top 20 rows



In [0]:
filtered_df.count()

2436

The code above shows that of the unique members in the 'dropped_play_df' dataframe, 2,436 of them (about 21%) have played 5 or more games. I will use this subset to train the recommender system 

In [0]:
# The filtered_df generated above only has 2 columns (memberID and count). I need to transform it back to the original 4-column layout (memberID, game, hours, and game ID), but keeping only the rows of players who played 4 or more games
filtered_full_df = dropped_play_df.join(filtered_df.select("memberID"), on="memberID", how="inner")

filtered_full_df.show()
filtered_full_df.count()

+---------+--------------------+-----+------+
| memberID|                game|hours|gameID|
+---------+--------------------+-----+------+
|151603712|The Elder Scrolls...|273.0|   8.0|
|151603712|           Fallout 4| 87.0| 100.0|
|151603712|               Spore| 14.9| 332.0|
|151603712|   Fallout New Vegas| 12.1|  29.0|
|151603712|       Left 4 Dead 2|  8.9|   4.0|
|151603712|            HuniePop|  8.5| 867.0|
|151603712|       Path of Exile|  8.1|  39.0|
|151603712|         Poly Bridge|  7.5|1347.0|
|151603712|         Left 4 Dead|  3.3|  49.0|
|151603712|     Team Fortress 2|  2.8|   1.0|
|151603712|         Tomb Raider|  2.5|  55.0|
|151603712|     The Banner Saga|  2.0| 604.0|
|151603712|Dead Island Epidemic|  1.4|  51.0|
|151603712|   BioShock Infinite|  1.3|  42.0|
|151603712|Dragon Age Origin...|  1.3| 301.0|
|151603712|Fallout 3 - Game ...|  0.8| 152.0|
|151603712|SEGA Genesis & Me...|  0.8| 655.0|
|151603712| Grand Theft Auto IV|  0.6|  43.0|
|151603712|Realm of the Mad God|  

57789

In [0]:
# split data in this filtered dataset into training and test dataset 

(training, test) = filtered_full_df.randomSplit([0.8, 0.2], seed=100)

# cache training dataset to speed up model training and hyperparameter tuning 
training.cache()

DataFrame[memberID: int, game: string, hours: double, gameID: double]

In [0]:
# Create another ALS model, train it on the training dataset containing data from players who played 4 or more games and eliminate negative predictions by including nonnegative=True

better_als = ALS(maxIter=5, regParam=0.01, userCol="memberID", itemCol="gameID", ratingCol='hours', nonnegative=True, seed=100)

better_model = better_als.fit(training)

# Use this new ALS model to generate predictions from the test dataset 

better_predictions = better_model.transform(test).dropna()


2025/04/06 10:00:18 INFO mlflow.utils.autologging_utils: Created MLflow autologging run with ID '28bb997218f24caea85e298095b533bc', which will track hyperparameters, performance metrics, model artifacts, and lineage information for the current pyspark.ml workflow
2025/04/06 10:00:34 WARNING mlflow.pyspark.ml: Model ALS_9179a1021213 will not be autologged because it is not allowlisted or or because one or more of its nested models are not allowlisted. Call mlflow.spark.log_model() to explicitly log the model, or specify a custom allowlist via the spark.mlflow.pysparkml.autolog.logModelAllowlistFile Spark conf (see mlflow.pyspark.ml.autolog docs for more info).


🏃 View run melodic-ox-333 at: https://community.cloud.databricks.com/ml/experiments/2194890496938728/runs/28bb997218f24caea85e298095b533bc
🧪 View experiment at: https://community.cloud.databricks.com/ml/experiments/2194890496938728


In [0]:
# measure how effective this model is by calculating RMSE

rmse = evaluator.evaluate(better_predictions)

print("Root Mean Square Error is %g" %rmse)

Root Mean Square Error is 403.488


Training the model on data from players who played 4 or more games and removing negative prediction values has improved its accuracy: the RMSE has been reduced from 561 to 403.

### Normalisation

In [0]:
# I will normalise the 'hours' column before re-running the ALS algorithm.  This is because in the original dataset, there is very high variance in this column (0.1 hours - 11,754 hours). The first ALS above might have overfit to users who have extremely high playtimes. Log transformation smooths out differences, improving generalisation and potentially reducing RMSE.

# from pyspark.sql.functions import log1p
# norm_play_df = filtered_full_df.withColumn("normalised_hours", log1p("hours"))

# split data in this normalised dataset into training and test dataset 

# (training, test) = norm_play_df.randomSplit([0.8, 0.2], seed=100)

# cache training dataset to speed up model training and hyperparameter tuning 
# training.cache()


I will now re-run the ALS model to see if these changes have made it more accurate. In addition to the above improvements, I will set ```nonnegative=True``` as it's not possible to have negative play durations, so negative numbers should not be generated in the predictions

In [0]:
# Create another ALS model using the improvements listed above and train it on the training dataset containing the normalised hours values 

# better_als = ALS(maxIter=5, regParam=0.01, userCol="memberID", itemCol="gameID", ratingCol='normalised_hours', nonnegative=True, seed=100)

# better_model = better_als.fit(training)

# Use this new ALS model to generate predictions from the test dataset 

# better_predictions = better_model.transform(test).dropna()





**1 MLflow RUN LOGGED - DISCUSS **

In [0]:
# better_predictions.show()

In [0]:
# from pyspark.sql.functions import expm1

# # Apply inverse transformation before evaluating RMSE
# predictions = better_predictions.withColumn("prediction_original", expm1("prediction"))

# # Use prediction_original instead of raw prediction for RMSE calculation
# rmse_evaluator = RegressionEvaluator(labelCol="hours", predictionCol="prediction_original", metricName="rmse")
# rmse = rmse_evaluator.evaluate(predictions)
# print(f"RMSE: {rmse}")


### Hyperparameter tuning
In this section, I will test different hyperparameter values to find the combination of hyperparameters that will make my model more accurate.  

First, I will import and instantiate the ParamGridBuilder, and then add the different values I want to try for the parameters to the grid. In this case, I am going to try:
- values of **XX, YY AND ZZ** for regParam (previously it was 0.01)
- values of **XX, YY AND ZZ** for rank (previously it was 10)
- values of **XX, YY AND ZZ** for maxIter (previously it was 5) 

In [0]:
# use 50% sample of training data to speed up gridsearch time 
# sample_training = training.sample(fraction=0.5, seed=42) 

# cache sample training dataset to speed up model training and hyperparameter tuning 
# sample_training.cache()


In [0]:
# Create a parameter grid to use for hyperparameter tuning 

from pyspark.ml.tuning import ParamGridBuilder

parameters = ParamGridBuilder().addGrid(als.regParam, [0.001, 0.01, 0.1, 0.2]).addGrid(als.rank, [5, 10, 20]).addGrid(als.maxIter, [5, 10, 15]).build()

In [0]:
# from pyspark.ml.tuning import CrossValidator

# crossval = CrossValidator(estimator=als, # could this use better_als?
#                           estimatorParamMaps=parameters,
#                           evaluator=evaluator,
#                           numFolds=5)  


In [0]:
# Define trainValidationSplit

from pyspark.ml.tuning import TrainValidationSplit

tvs = TrainValidationSplit()\
    .setSeed(100)\
    .setTrainRatio(0.75)\
    .setEstimatorParamMaps(parameters)\
    .setEstimator(better_als)\
    .setEvaluator(evaluator)

In [0]:
# Train model using grid search

gridsearchModel = tvs.fit(training)

2025/04/06 10:21:35 INFO mlflow.utils.autologging_utils: Created MLflow autologging run with ID '8367a9164ee34674b5cd6d303a6e1655', which will track hyperparameters, performance metrics, model artifacts, and lineage information for the current pyspark.ml workflow


🏃 View run grandiose-koi-883 at: https://community.cloud.databricks.com/ml/experiments/2194890496938728/runs/8367a9164ee34674b5cd6d303a6e1655
🧪 View experiment at: https://community.cloud.databricks.com/ml/experiments/2194890496938728


2025/04/06 10:29:58 WARNING mlflow.utils.autologging_utils: Encountered unexpected error during pyspark.ml autologging: Tuning params should not include params not owned by the tuned estimator, but found a param ALS_21e31cce0c18__regParam


**MLflow LOGGED 16 RUNS - DISCUSS**

In [0]:
# Print the optimal hyperparameters as determined by the grid search 

bestModel = gridsearchModel.bestModel

print("Parameters for the best model:")
print("Rank Parameter: %g" %bestModel.rank)
print("RegParam Parameter: %g" %bestModel._java_obj.parent().getRegParam())
print("maxIter Parameter: %g" %bestModel._java_obj.parent().getMaxIter())


Parameters for the best model:
Rank Parameter: 10
RegParam Parameter: 0.01
maxIter Parameter: 5


[This run](https://community.cloud.databricks.com/ml/experiments/2194890496938728/runs/01f15a8ca93046e48b642a13f51ee8af?o=443721649673591) was XYZZ...


In [0]:
# Create another ALS model using the optimal hyperparameters as determined by the grid search and the other improvements listed above 

best_als = ALS(maxIter=5, regParam=0.01, rank=10, userCol="memberID", itemCol="gameID", ratingCol='hours', nonnegative=True, seed=100)

best_model = best_als.fit(training)

# Use this new ALS model to generate predictions from the test dataset 

best_predictions = best_model.transform(test).dropna()

2025/04/06 10:20:50 INFO mlflow.utils.autologging_utils: Created MLflow autologging run with ID '5e0d108523664685aea36a354e596383', which will track hyperparameters, performance metrics, model artifacts, and lineage information for the current pyspark.ml workflow
2025/04/06 10:20:51 WARNING mlflow.utils.autologging_utils: MLflow autologging encountered a warning: "/databricks/python/lib/python3.11/site-packages/mlflow/types/utils.py:435: UserWarning: Hint: Inferred schema contains integer column(s). Integer columns in Python cannot represent missing values. If your input data contains missing values at inference time, it will be encoded as floats and will cause a schema enforcement error. The best way to avoid this problem is to infer the model schema based on a realistic data sample (training dataset) that includes missing values. Alternatively, you can declare integer columns as doubles (float64) whenever these columns may have missing values. See `Handling Integers With Missing Valu

🏃 View run handsome-swan-27 at: https://community.cloud.databricks.com/ml/experiments/2194890496938728/runs/5e0d108523664685aea36a354e596383
🧪 View experiment at: https://community.cloud.databricks.com/ml/experiments/2194890496938728


**1 MLflow run logged - discuss**

In [0]:
# Calculate root mean square error value for this best model 

rmse = evaluator.evaluate(best_predictions)

print("Root Mean Square Error is %g" %rmse)

Root Mean Square Error is 403.488


## Generating Recommendations

In [0]:
# use the best model (according to the hyperparameter tuning grid search) to generate predictions  
loaded_predictions = loaded_model.transform(test)
loaded_predictions.show()

To generate predictions, I will create a new DataFrame which contains all the gameIDs and a column populated with a new memberID of ‘0’. I will then use the transform method on this data, which will generate a prediction for the member with memberID 0 for every game in the dataset. I can then use orderBy to sort on the games with the highest values for predicted play durationn – these are the games which member0 is predicted to play the most.

In [0]:
# Create new dataframe will all gameIDs and names, and '0' in the memberID column 

unique_games_df = dropped_play_df.select("game", "gameID").dropDuplicates()
unique_games_df.show()

+--------------------+------+
|                game|gameID|
+--------------------+------+
|            HuniePop| 867.0|
|               Spore| 332.0|
|  Marvel Heroes 2015|  73.0|
|The Elder Scrolls...|   8.0|
|             Eldevin| 881.0|
|Fallout 3 - Game ...| 152.0|
|SEGA Genesis & Me...| 655.0|
|           Fallout 4| 100.0|
| Grand Theft Auto IV|  43.0|
|         Left 4 Dead|  49.0|
|         Tomb Raider|  55.0|
|       Left 4 Dead 2|   4.0|
|         Poly Bridge|1347.0|
|   BioShock Infinite|  42.0|
|Dragon Age Origin...| 301.0|
|     Team Fortress 2|   1.0|
|       Path of Exile|  39.0|
|   Fallout New Vegas|  29.0|
|Realm of the Mad God| 134.0|
|     The Banner Saga| 604.0|
+--------------------+------+
only showing top 20 rows



In [0]:
myGeneratedPredictions = unique_games_df.withColumn("memberID", functions.expr("int('0')"))
myGeneratedPredictions.show()

+--------------------+------+--------+
|                game|gameID|memberID|
+--------------------+------+--------+
|            HuniePop| 867.0|       0|
|               Spore| 332.0|       0|
|  Marvel Heroes 2015|  73.0|       0|
|The Elder Scrolls...|   8.0|       0|
|             Eldevin| 881.0|       0|
|Fallout 3 - Game ...| 152.0|       0|
|SEGA Genesis & Me...| 655.0|       0|
|           Fallout 4| 100.0|       0|
| Grand Theft Auto IV|  43.0|       0|
|         Left 4 Dead|  49.0|       0|
|         Tomb Raider|  55.0|       0|
|       Left 4 Dead 2|   4.0|       0|
|         Poly Bridge|1347.0|       0|
|   BioShock Infinite|  42.0|       0|
|Dragon Age Origin...| 301.0|       0|
|     Team Fortress 2|   1.0|       0|
|       Path of Exile|  39.0|       0|
|   Fallout New Vegas|  29.0|       0|
|Realm of the Mad God| 134.0|       0|
|     The Banner Saga| 604.0|       0|
+--------------------+------+--------+
only showing top 20 rows



In [0]:
# use the best model to generate recommendations

myGeneratedPredictions = better_model.transform(myGeneratedPredictions)

myGeneratedPredictions = myGeneratedPredictions.dropna()

myGeneratedPredictions.orderBy("prediction",ascending=False).show(10)

---------------------------------------------------------------------------
IllegalArgumentException                  Traceback (most recent call last)
File <command-4608006875796>, line 3
      1 # use the best model to generate recommendations
----> 3 myGeneratedPredictions = better_model.transform(myGeneratedPredictions)
      5 myGeneratedPredictions.orderBy("prediction",ascending=False).show(10)

File /databricks/python/lib/python3.11/site-packages/mlflow/utils/autologging_utils/safety.py:592, in safe_patch.<locals>.safe_patch_function(*args, **kwargs)
    590     patch_function.call(call_original, *args, **kwargs)
    591 else:
--> 592     patch_function(call_original, *args, **kwargs)
    594 session.state = "succeeded"
    596 try_log_autologging_event(
    597     AutologgingEventLogger.get_logger().log_patch_function_success,
    598     session,
   (...)
    602     kwargs,
    603 )

File /databricks/python/lib/python3.11/site-packages/mlflow/pyspark/ml/__init__.py:1177, in

Use a markdown cell at the end of the question to briefly explain the output / relate this back to the question and to comment or explain anything significant about this finding. Follow this structure (or a similar structure) for all questions / sections of your submission.

If you want to add additional markdown cells to provide further explanation throughout your notebook, add these as required.

REFLECTION: COULD TRY USING PURCHASE DATA AS WELL AS PLAY DATA TO REFINE RECOMMENDATIONS? 

## Conclusion

Finish with a brief conclusion to wrap up your submission and any key findings.